In [1]:
import folium
import osmnx as ox
import pandas as pd

In [2]:
# Dictionary of station coordinates (latitude, longitude)
station_coords = {
    'Ebersheim': (49.9275, 8.3458),
    'Finthen': (49.9733, 8.1750),
    'Gonsenheim': (49.9833, 8.2167),
    'Hartenberg': (49.9833, 8.2667),
    'Hechtsheim': (49.9667, 8.2500),
    'Laubenheim': (49.9333, 8.3000),
    'Lerchenberg': (49.9833, 8.2333),
    'Marienborn': (49.9667, 8.2167),
    'Mombach': (49.9833, 8.2167),
    'Neustadt': (49.9833, 8.2667),
    'Oberstadt': (49.9833, 8.2667),
    'Weisenau': (49.9667, 8.2833)
}

In [3]:
# Create a map centered on Mainz
m = folium.Map(location=[49.9833, 8.2667], zoom_start=12)
m

In [4]:
# Add markers and coverage areas for each station
for station, coords in station_coords.items():
    # Add marker
    folium.Marker(
        location=coords,
        popup=station,
        icon=folium.Icon(color='red', icon='info-sign')
    ).add_to(m)
    
    # Add coverage area (500m radius)
    folium.Circle(
        location=coords,
        radius=500,
        color='blue',
        fill=True,
        fill_color='blue',
        fill_opacity=0.2,
        popup=f'{station} Coverage Area'
    ).add_to(m)

# Display the map again to see the updates
m

In [5]:
# Download the street network for Mainz and overlay it on the map
G = ox.graph_from_place('Mainz, Germany', network_type='drive')
ox.plot_graph_folium(G, graph_map=m, color='gray', weight=2, opacity=0.5)

# Show the map with the street network
m

In [7]:
# Load all station data files
import glob
import os

# Get the path to the data directory
data_dir = os.path.join(os.path.dirname(os.getcwd()), 'data')

# Find all monthly means files
station_files = glob.glob(os.path.join(data_dir, 'monthly_means_*.csv'))

# Dictionary to store data for each station
station_data = {}
years = set()

# Load data for each station
for file in station_files:
    station_name = os.path.basename(file).replace('monthly_means_', '').replace('.csv', '')
    try:
        df = pd.read_csv(file)
        # Convert month_year to datetime
        df['date'] = pd.to_datetime(df['month_year'])
        # Extract year
        df['year'] = df['date'].dt.year
        years.update(df['year'].unique())
        station_data[station_name] = df
        print(f"Loaded data for {station_name}")
    except Exception as e:
        print(f"Error loading {station_name}: {str(e)}")

years = sorted(list(years))
print("\nAvailable years:", years)

Loaded data for weather
Loaded data for Weisenau_2_ooo
Loaded data for Lerchenberg_ooo
Loaded data for Laubenheim_ooo
Loaded data for Hechtsheim_1_ooo
Loaded data for Lerchenberg
Loaded data for Laubenheim_2
Loaded data for Ebersheim
Loaded data for Oberstadt_ooo
Loaded data for Bretzenheim_ooo
Loaded data for Hechtsheim_2

Available years: [2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020, 2021, 2022, 2023, 2024]


/var/folders/vr/j882mf891_d5jrypcnk4y3340000gn/T/ipykernel_95168/114753871.py:21: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df['date'] = pd.to_datetime(df['month_year'])
/var/folders/vr/j882mf891_d5jrypcnk4y3340000gn/T/ipykernel_95168/114753871.py:21: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df['date'] = pd.to_datetime(df['month_year'])
/var/folders/vr/j882mf891_d5jrypcnk4y3340000gn/T/ipykernel_95168/114753871.py:21: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df['date'] = pd.to_datetime(df['month_year'])
/var/folders/vr/j882mf891_d5jrypcnk4y3340000gn/T/ipykernel

In [9]:
# Create a function to update the map based on selected year
def create_map_for_year(year):
    # Create a new map centered on Mainz
    m = folium.Map(location=[49.9833, 8.2667], zoom_start=12)
    
    # Add street network
    G = ox.graph_from_place('Mainz, Germany', network_type='drive')
    ox.plot_graph_folium(G, graph_map=m, color='gray', weight=2, opacity=0.5)
    
    # Add markers and coverage areas for each station
    for station, coords in station_coords.items():
        # Get data for the selected year
        if station in station_data:
            year_data = station_data[station][station_data[station]['year'] == year]
            if not year_data.empty:
                # Calculate mean value for the year
                mean_value = year_data['db_a'].mean()  # Adjust column name if needed
                
                # Add marker with popup showing station name and mean value
                folium.Marker(
                    location=coords,
                    popup=f"{station}<br>Mean Value: {mean_value:.2f}",
                    icon=folium.Icon(color='red', icon='info-sign')
                ).add_to(m)
                
                # Add coverage area (500m radius)
                folium.Circle(
                    location=coords,
                    radius=500,
                    color='blue',
                    fill=True,
                    fill_color='blue',
                    fill_opacity=0.2,
                    popup=f'{station} Coverage Area'
                ).add_to(m)
    
    return m



In [11]:
# Create an interactive map with year selection
from ipywidgets import interact, Dropdown

# Create a dropdown for year selection
year_dropdown = Dropdown(
    options=years,
    value=years[0],
    description='Select Year:',
    style={'description_width': 'initial'}
)

# Function to update map when year is selected
def update_map(year):
    return create_map_for_year(year)


In [15]:
# Import required libraries
import folium
import osmnx as ox
import pandas as pd
import glob
import os
from ipywidgets import interact, Dropdown
from datetime import datetime

# Define station coordinates
station_coords = {
    'Ebersheim': (49.9275, 8.3458),
    'Finthen': (49.9733, 8.1750),
    'Gonsenheim': (49.9833, 8.2167),
    'Hartenberg': (49.9833, 8.2667),
    'Hechtsheim': (49.9667, 8.2500),
    'Laubenheim': (49.9333, 8.3000),
    'Lerchenberg': (49.9833, 8.2333),
    'Marienborn': (49.9667, 8.2167),
    'Mombach': (49.9833, 8.2167),
    'Neustadt': (49.9833, 8.2667),
    'Oberstadt': (49.9833, 8.2667),
    'Weisenau': (49.9667, 8.2833),
    'Bretzenheim': (49.9833, 8.2333)
}

# Load all station data files
data_dir = os.path.join(os.path.dirname(os.getcwd()), 'data')
station_files = glob.glob(os.path.join(data_dir, 'monthly_means_*.csv'))

# Dictionary to store data for each station
station_data = {}
years = set()

# Function to convert month-year string to datetime
def parse_month_year(date_str):
    try:
        return datetime.strptime(date_str, '%B %Y')
    except ValueError:
        return None

# Load data for each station
for file in station_files:
    station_name = os.path.basename(file).replace('monthly_means_', '').replace('.csv', '')
    try:
        df = pd.read_csv(file)
        # Convert month_year to datetime
        df['date'] = df['month_year'].apply(parse_month_year)
        # Extract year
        df['year'] = df['date'].dt.year
        years.update(df['year'].unique())
        station_data[station_name] = df
        print(f"Loaded data for {station_name}")
    except Exception as e:
        print(f"Error loading {station_name}: {str(e)}")

years = sorted(list(years))
print("\nAvailable years:", years)

# Function to create map for a specific year
def create_map_for_year(year):
    # Create a new map centered on Mainz
    m = folium.Map(location=[49.9833, 8.2667], zoom_start=12)
    
    # Add street network
    G = ox.graph_from_place('Mainz, Germany', network_type='drive')
    ox.plot_graph_folium(G, graph_map=m, color='gray', weight=2, opacity=0.5)
    
    # Add markers and coverage areas for each station
    for station, coords in station_coords.items():
        # Find matching station data
        matching_stations = [s for s in station_data.keys() if station.lower() in s.lower()]
        
        if matching_stations:
            for matching_station in matching_stations:
                year_data = station_data[matching_station][station_data[matching_station]['year'] == year]
                if not year_data.empty:
                    # Calculate mean value for the year
                    mean_value = year_data['db_a'].mean()
                    
                    # Add marker with popup showing station name and mean value
                    folium.Marker(
                        location=coords,
                        popup=f"{matching_station}<br>Mean Value: {mean_value:.2f}",
                        icon=folium.Icon(color='red', icon='info-sign')
                    ).add_to(m)
                    
                    # Add coverage area (500m radius)
                    folium.Circle(
                        location=coords,
                        radius=500,
                        color='blue',
                        fill=True,
                        fill_color='blue',
                        fill_opacity=0.2,
                        popup=f'{matching_station} Coverage Area'
                    ).add_to(m)
    
    return m

# Create interactive year selection
year_dropdown = Dropdown(
    options=years,
    value=years[0],
    description='Select Year:',
    style={'description_width': 'initial'}
)

# Function to update map when year is selected
def update_map(year):
    return create_map_for_year(year)

# Create the interactive widget
interact(update_map, year=year_dropdown)

Loaded data for weather
Loaded data for Weisenau_2_ooo
Loaded data for Lerchenberg_ooo
Loaded data for Laubenheim_ooo
Loaded data for Hechtsheim_1_ooo
Loaded data for Lerchenberg
Loaded data for Laubenheim_2
Loaded data for Ebersheim
Loaded data for Oberstadt_ooo
Loaded data for Bretzenheim_ooo
Loaded data for Hechtsheim_2

Available years: [2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020, 2021, 2022, 2023, 2024]


interactive(children=(Dropdown(description='Select Year:', options=(2012, 2013, 2014, 2015, 2016, 2017, 2018, …

<function __main__.update_map(year)>

In [16]:
# Import required libraries
import folium
import osmnx as ox
import pandas as pd
import glob
import os
from ipywidgets import interact, Dropdown
from datetime import datetime
from folium.plugins import HeatMap

# Define station coordinates
station_coords = {
    'Ebersheim': (49.9275, 8.3458),
    'Finthen': (49.9733, 8.1750),
    'Gonsenheim': (49.9833, 8.2167),
    'Hartenberg': (49.9833, 8.2667),
    'Hechtsheim': (49.9667, 8.2500),
    'Laubenheim': (49.9333, 8.3000),
    'Lerchenberg': (49.9833, 8.2333),
    'Marienborn': (49.9667, 8.2167),
    'Mombach': (49.9833, 8.2167),
    'Neustadt': (49.9833, 8.2667),
    'Oberstadt': (49.9833, 8.2667),
    'Weisenau': (49.9667, 8.2833),
    'Bretzenheim': (49.9833, 8.2333)
}

# Load all station data files
data_dir = os.path.join(os.path.dirname(os.getcwd()), 'data')
station_files = glob.glob(os.path.join(data_dir, 'monthly_means_*.csv'))

# Dictionary to store data for each station
station_data = {}
years = set()

# Function to convert month-year string to datetime
def parse_month_year(date_str):
    try:
        return datetime.strptime(date_str, '%B %Y')
    except ValueError:
        return None

# Load data for each station
for file in station_files:
    station_name = os.path.basename(file).replace('monthly_means_', '').replace('.csv', '')
    try:
        df = pd.read_csv(file)
        # Convert month_year to datetime
        df['date'] = df['month_year'].apply(parse_month_year)
        # Extract year
        df['year'] = df['date'].dt.year
        years.update(df['year'].unique())
        station_data[station_name] = df
        print(f"Loaded data for {station_name}")
    except Exception as e:
        print(f"Error loading {station_name}: {str(e)}")

years = sorted(list(years))
print("\nAvailable years:", years)

# Function to create map for a specific year
def create_map_for_year(year):
    # Create a new map centered on Mainz
    m = folium.Map(location=[49.9833, 8.2667], zoom_start=12)
    
    # Add street network
    G = ox.graph_from_place('Mainz, Germany', network_type='drive')
    ox.plot_graph_folium(G, graph_map=m, color='gray', weight=2, opacity=0.5)
    
    # Prepare heatmap data
    heat_data = []
    
    # Add data points for each station
    for station, coords in station_coords.items():
        # Find matching station data
        matching_stations = [s for s in station_data.keys() if station.lower() in s.lower()]
        
        if matching_stations:
            for matching_station in matching_stations:
                year_data = station_data[matching_station][station_data[matching_station]['year'] == year]
                if not year_data.empty:
                    # Calculate mean value for the year
                    mean_value = year_data['db_a'].mean()
                    # Add to heatmap data with weight based on noise level
                    heat_data.append([coords[0], coords[1], mean_value])
    
    # Add heatmap layer
    HeatMap(heat_data, 
            min_opacity=0.5,
            max_val=max([d[2] for d in heat_data]),
            radius=25, 
            blur=15, 
            max_zoom=1).add_to(m)
    
    # Add markers with popups for reference
    for station, coords in station_coords.items():
        matching_stations = [s for s in station_data.keys() if station.lower() in s.lower()]
        if matching_stations:
            for matching_station in matching_stations:
                year_data = station_data[matching_station][station_data[matching_station]['year'] == year]
                if not year_data.empty:
                    mean_value = year_data['db_a'].mean()
                    folium.Marker(
                        location=coords,
                        popup=f"{matching_station}<br>Mean Noise Level: {mean_value:.2f} dB",
                        icon=folium.Icon(color='red', icon='info-sign')
                    ).add_to(m)
    
    return m

# Create interactive year selection
year_dropdown = Dropdown(
    options=years,
    value=years[0],
    description='Select Year:',
    style={'description_width': 'initial'}
)

# Function to update map when year is selected
def update_map(year):
    return create_map_for_year(year)

# Create the interactive widget
interact(update_map, year=year_dropdown)

Loaded data for weather
Loaded data for Weisenau_2_ooo
Loaded data for Lerchenberg_ooo
Loaded data for Laubenheim_ooo
Loaded data for Hechtsheim_1_ooo
Loaded data for Lerchenberg
Loaded data for Laubenheim_2
Loaded data for Ebersheim
Loaded data for Oberstadt_ooo
Loaded data for Bretzenheim_ooo
Loaded data for Hechtsheim_2

Available years: [2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020, 2021, 2022, 2023, 2024]


interactive(children=(Dropdown(description='Select Year:', options=(2012, 2013, 2014, 2015, 2016, 2017, 2018, …

<function __main__.update_map(year)>

In [ ]:
# Import required libraries
import folium
import osmnx as ox
import pandas as pd
import glob
import os
from ipywidgets import interact, Dropdown
from datetime import datetime
from folium.plugins import HeatMap

# Define station coordinates
station_coords = {
    'Ebersheim': (49.9275, 8.3458),
    'Finthen': (49.9733, 8.1750),
    'Gonsenheim': (49.9833, 8.2167),
    'Hartenberg': (49.9833, 8.2667),
    'Hechtsheim': (49.9667, 8.2500),
    'Laubenheim': (49.9333, 8.3000),
    'Lerchenberg': (49.9833, 8.2333),
    'Marienborn': (49.9667, 8.2167),
    'Mombach': (49.9833, 8.2167),
    'Neustadt': (49.9833, 8.2667),
    'Oberstadt': (49.9833, 8.2667),
    'Weisenau': (49.9667, 8.2833),
    'Bretzenheim': (49.9833, 8.2333)
}

# Load all station data files
data_dir = os.path.join(os.path.dirname(os.getcwd()), 'data')
station_files = glob.glob(os.path.join(data_dir, 'monthly_means_*.csv'))

# Dictionary to store data for each station
station_data = {}
years = set()

# Function to convert month-year string to datetime
def parse_month_year(date_str):
    try:
        return datetime.strptime(date_str, '%B %Y')
    except ValueError:
        return None

# Load data for each station
for file in station_files:
    station_name = os.path.basename(file).replace('monthly_means_', '').replace('.csv', '')
    try:
        df = pd.read_csv(file)
        # Convert month_year to datetime
        df['date'] = df['month_year'].apply(parse_month_year)
        # Extract year
        df['year'] = df['date'].dt.year
        years.update(df['year'].unique())
        station_data[station_name] = df
        print(f"Loaded data for {station_name}")
    except Exception as e:
        print(f"Error loading {station_name}: {str(e)}")

years = sorted(list(years))
print("\nAvailable years:", years)

# Function to get heatmap data for a specific year
def get_heatmap_data(year):
    heat_data = []
    for station, coords in station_coords.items():
        matching_stations = [s for s in station_data.keys() if station.lower() in s.lower()]
        if matching_stations:
            for matching_station in matching_stations:
                year_data = station_data[matching_station][station_data[matching_station]['year'] == year]
                if not year_data.empty:
                    mean_value = year_data['db_a'].mean()
                    heat_data.append([coords[0], coords[1], mean_value])
    return heat_data

# Function to create map for a specific year
def create_map_for_year(year):
    # Create a new map centered on Mainz
    m = folium.Map(location=[49.9833, 8.2667], zoom_start=12)
    
    # Add street network
    G = ox.graph_from_place('Mainz, Germany', network_type='drive')
    ox.plot_graph_folium(G, graph_map=m, color='gray', weight=2, opacity=0.5)
    
    # Get heatmap data for the selected year
    heat_data = get_heatmap_data(year)
    
    if heat_data:
        # Add heatmap layer
        HeatMap(heat_data, 
                min_opacity=0.5,
                radius=25, 
                blur=15, 
                max_zoom=1).add_to(m)
        
        # Add markers with popups for reference
        for station, coords in station_coords.items():
            matching_stations = [s for s in station_data.keys() if station.lower() in s.lower()]
            if matching_stations:
                for matching_station in matching_stations:
                    year_data = station_data[matching_station][station_data[matching_station]['year'] == year]
                    if not year_data.empty:
                        mean_value = year_data['db_a'].mean()
                        folium.Marker(
                            location=coords,
                            popup=f"{matching_station}<br>Mean Noise Level: {mean_value:.2f} dB",
                            icon=folium.Icon(color='red', icon='info-sign')
                        ).add_to(m)
    
    return m

# Create interactive year selection
year_dropdown = Dropdown(
    options=years,
    value=years[0],
    description='Select Year:',
    style={'description_width': 'initial'}
)

# Function to update map when year is selected
def update_map(year):
    return create_map_for_year(year)

# Create the interactive widget
interact(update_map, year=year_dropdown)

Loaded data for weather
Loaded data for Weisenau_2_ooo
Loaded data for Lerchenberg_ooo
Loaded data for Laubenheim_ooo
Loaded data for Hechtsheim_1_ooo
Loaded data for Lerchenberg
Loaded data for Laubenheim_2
Loaded data for Ebersheim
Loaded data for Oberstadt_ooo
Loaded data for Bretzenheim_ooo
Loaded data for Hechtsheim_2

Available years: [2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020, 2021, 2022, 2023, 2024]
